In [19]:
import random
import math
from environment import Agent, Environment
from planner import RoutePlanner
from simulator import Simulator

class LearningAgent(Agent):
    """ An agent that learns to drive in the Smartcab world.
        This is the object you will be modifying. """ 

    def __init__(self, env, learning=False, epsilon=1.0, alpha=0.5):
        super(LearningAgent, self).__init__(env)     # Set the agent in the evironment 
        self.planner = RoutePlanner(self.env, self)  # Create a route planner
        self.valid_actions = self.env.valid_actions  # The set of valid actions

        # Set parameters of the learning agent
        self.learning = learning # Whether the agent is expected to learn
        self.Q = dict()          # Create a Q-table which will be a dictionary of tuples
        self.epsilon = epsilon   # Random exploration factor
        self.alpha = alpha       # Learning factor

        ###########
        ## TO DO ##
        ###########
        # Set any additional class parameters as needed
        self.trial = 0
        random.seed(22)


    def reset(self, destination=None, testing=False):
        """ The reset function is called at the beginning of each trial.
            'testing' is set to True if testing trials are being used
            once training trials have completed. """

        # Select the destination as the new location to route to
        self.planner.route_to(destination)
        
        ########### 
        ## TO DO ##
        ###########
        # Update epsilon using a decay function of your choice
        # Update additional class parameters as needed
        # If 'testing' is True, set epsilon and alpha to 0
        # self.epsilon = self.epsilon-0.05
        
        if testing == 'True':
            self.epsilon = 0
            self.alpha = 0
        else:
            self.trial += 1
            # self.epsilon = 1/(self.trial**2)
            # Safety Rating - F, Reliability Rating - B. Zig Zag curves. This is no better than linear decay factor.
            # But the reliability rating has improved to B
            # self.epsilon = math.cos(self.alpha*self.trial) -> Safety F and Reliability - F
            # self.epsilon = (self.alpha**self.trial) -> Ssfety C and Reliability C
            # self.epsilon = 0.90 ** self.trial -> Safety F and Reliability C
            # self.epsilon = 1/(self.trial**2) # -> Safety F and Reliability C
            self.epsilon = math.cos(self.alpha*self.trial) #
            # self.epsilon = 0.98**self.trial 

        return None

    def build_state(self):
        """ The build_state function is called when the agent requests data from the 
            environment. The next waypoint, the intersection inputs, and the deadline 
            are all features available to the agent. """

        # Collect data about the environment
        waypoint = self.planner.next_waypoint() # The next waypoint 
        inputs = self.env.sense(self)           # Visual input - intersection light and traffic
        deadline = self.env.get_deadline(self)  # Remaining deadline

        ########### 
        ## TO DO ##
        ###########
        
        # NOTE : you are not allowed to engineer eatures outside of the inputs available.
        # Because the aim of this project is to teach Reinforcement Learning, we have placed 
        # constraints in order for you to learn how to adjust epsilon and alpha, and thus learn about the balance between exploration and exploitation.
        # With the hand-engineered features, this learning process gets entirely negated.
        
        # Set 'state' as a tuple of relevant data for the agent        
        state = (waypoint,inputs['light'],inputs['left'], inputs['oncoming'])
        return state


    def get_maxQ(self, state):
        """ The get_max_Q function is called when the agent is asked to find the
            maximum Q-value of all actions based on the 'state' the smartcab is in. """

        ########### 
        ## TO DO ##
        ###########
        # Calculate the maximum Q-value of all actions for a given state

        maxQ = max(self.Q[state].values())

        return maxQ


    def createQ(self, state):
        """ The createQ function is called when a state is generated by the agent. """

        ########### 
        ## TO DO ##
        ###########
        # When learning, check if the 'state' is not in the Q-table
        # If it is not, create a new dictionary for that state
        #   Then, for each action available, set the initial Q-value to 0.0
        
        print("state variables below")
        print(state)
        print(self.Q.keys)
        if self.learning == True:
            if state not in self.Q.keys():
                self.Q[state] = {}
                for action in self.valid_actions:
                    self.Q[state][action] = 0.0

        return


    def choose_action(self, state):
        """ The choose_action function is called when the agent is asked to choose
            which action to take, based on the 'state' the smartcab is in. """

        # Set the agent state and default action
        self.state = state
        self.next_waypoint = self.planner.next_waypoint()
        action = None

        ########### 
        ## TO DO ##
        ###########
        # When not learning, choose a random action
        # When learning, choose a random action with 'epsilon' probability
        # Otherwise, choose an action with the highest Q-value for the current state
        # Be sure that when choosing an action with highest Q-value that you randomly select between actions that "tie".
        if not self.learning:
            action = random.choice(self.valid_actions)
        else:
            if self.epsilon > 0.01 and self.epsilon > random.random():
                action = random.choice(self.valid_actions)
            else:
                action = max(self.Q[state], key=self.Q[state].get)
        return action


    def learn(self, state, action, reward):
        """ The learn function is called after the agent completes an action and
            receives a reward. This function does not consider future rewards 
            when conducting learning. """

        ########### 
        ## TO DO ##
        ###########
        # When learning, implement the value iteration update rule
        #   Use only the learning rate 'alpha' (do not use the discount factor 'gamma')
        if self.learning == True:
            self.Q[state][action] = self.Q[state][action] + self.alpha*(reward - self.Q[state][action])

        return


    def update(self):
        """ The update function is called when a time step is completed in the 
            environment for a given trial. This function will build the agent
            state, choose an action, receive a reward, and learn if enabled. """

        state = self.build_state()          # Get current state
        self.createQ(state)                 # Create 'state' in Q-table
        action = self.choose_action(state)  # Choose an action
        reward = self.env.act(self, action) # Receive a reward
        self.learn(state, action, reward)   # Q-learn

        return
        

def run():
    """ Driving function for running the simulation. 
        Press ESC to close the simulation, or [SPACE] to pause the simulation. """

    ##############
    # Create the environment
    # Flags:
    #   verbose     - set to True to display additional output from the simulation
    #   num_dummies - discrete number of dummy agents in the environment, default is 100
    #   grid_size   - discrete number of intersections (columns, rows), default is (8, 6)
    env = Environment(verbose=True)
    
    ##############
    # Create the driving agent
    # Flags:
    #   learning   - set to True to force the driving agent to use Q-learning
    #    * epsilon - continuous value for the exploration factor, default is 1
    #    * alpha   - continuous value for the learning rate, default is 0.5
    agent = env.create_agent(LearningAgent, learning=True, alpha = 0.01)
    
    ##############
    # Follow the driving agent
    # Flags:
    #   enforce_deadline - set to True to enforce a deadline metric
    env.set_primary_agent(agent, enforce_deadline=True)

    ##############
    # Create the simulation
    # Flags:
    #   update_delay - continuous time (in seconds) between actions, default is 2.0 seconds
    #   display      - set to False to disable the GUI if PyGame is enabled
    #   log_metrics  - set to True to log trial and simulation results to /logs
    #   optimized    - set to True to change the default log file name
    sim = Simulator(env, update_delay=0.01, log_metrics=True,optimized=True)
    
    ##############
    # Run the simulator
    # Flags:
    #   tolerance  - epsilon tolerance before beginning testing, default is 0.05 
    #   n_test     - discrete number of testing trials to perform, default is 0
    sim.run(n_test=100, tolerance = 0.001)

if __name__ == '__main__':
    run()

Simulator.__init__(): Error initializing GUI objects; display disabled.
error: Couldn't open images/logo.png

/-------------------------
| Training trial 1
\-------------------------

Environment.reset(): Trial set up with start = (8, 7), destination = (2, 4), deadline = 25
Simulating trial. . . 
epsilon = 1.0000; alpha = 0.0100
Simulating trial. . . 
epsilon = 1.0000; alpha = 0.0100
Simulating trial. . . 
epsilon = 1.0000; alpha = 0.0100
Simulating trial. . . 
epsilon = 1.0000; alpha = 0.0100
Simulating trial. . . 
epsilon = 1.0000; alpha = 0.0100
Simulating trial. . . 
epsilon = 1.0000; alpha = 0.0100
Simulating trial. . . 
epsilon = 1.0000; alpha = 0.0100
Simulating trial. . . 
epsilon = 1.0000; alpha = 0.0100
Simulating trial. . . 
epsilon = 1.0000; alpha = 0.0100
Simulating trial. . . 
epsilon = 1.0000; alpha = 0.0100
Simulating trial. . . 
epsilon = 1.0000; alpha = 0.0100
Simulating trial. . . 
epsilon = 1.0000; alpha = 0.0100
Simulating trial. . . 
epsilon = 1.0000; alpha = 0.01

52% of time remaining to reach destination.

/-------------------
| Step 12 Results
\-------------------

Environment.step(): t = 12
state variables below
('left', 'red', None, 'forward')
<built-in method keys of dict object at 0x114faab40>
Environment.act() [POST]: location: (6, 7), heading: (0, -1), action: right, reward: -0.0627063439039
Environment.act(): Step data: {'inputs': {'light': 'red', 'oncoming': 'forward', 'right': None, 'left': None}, 'violation': 0, 'light': 'red', 'state': ('left', 'red', None, 'forward'), 'deadline': 13, 't': 12, 'action': 'right', 'reward': -0.06270634390387397, 'waypoint': 'left'}
Agent previous state: ('left', 'red', None, 'forward')
Agent drove right instead of left. (rewarded -0.06)
48% of time remaining to reach destination.

/-------------------
| Step 13 Results
\-------------------

Environment.step(): t = 13
state variables below
('right', 'green', None, 'forward')
<built-in method keys of dict object at 0x114faab40>
Environment.act() [POST]

('left', 'red', None, 'left')
<built-in method keys of dict object at 0x114faab40>
Environment.act() [POST]: location: (2, 5), heading: (0, -1), action: None, reward: 1.40408285805
Environment.act(): Step data: {'inputs': {'light': 'red', 'oncoming': 'left', 'right': 'forward', 'left': None}, 'violation': 0, 'light': 'red', 'state': ('left', 'red', None, 'left'), 'deadline': 19, 't': 1, 'action': None, 'reward': 1.4040828580494322, 'waypoint': 'left'}
Agent previous state: ('left', 'red', None, 'left')
Agent properly idled at a red light. (rewarded 1.40)
90% of time remaining to reach destination.

/-------------------
| Step 2 Results
\-------------------

Environment.step(): t = 2
state variables below
('left', 'red', 'right', 'left')
<built-in method keys of dict object at 0x114faab40>
Environment.act() [POST]: location: (2, 5), heading: (0, -1), action: left, reward: -9.47847514249
Environment.act(): Step data: {'inputs': {'light': 'red', 'oncoming': 'left', 'right': None, 'left': 

epsilon = 0.9996; alpha = 0.0100
Simulating trial. . . 
epsilon = 0.9996; alpha = 0.0100
Simulating trial. . . 
epsilon = 0.9996; alpha = 0.0100
Simulating trial. . . 
epsilon = 0.9996; alpha = 0.0100
Simulating trial. . . 
epsilon = 0.9996; alpha = 0.0100
Simulating trial. . . 
epsilon = 0.9996; alpha = 0.0100
Simulating trial. . . 
epsilon = 0.9996; alpha = 0.0100
Simulating trial. . . 
epsilon = 0.9996; alpha = 0.0100
Simulating trial. . . 
epsilon = 0.9996; alpha = 0.0100
Simulating trial. . . 
epsilon = 0.9996; alpha = 0.0100
Simulating trial. . . 
epsilon = 0.9996; alpha = 0.0100
Simulating trial. . . 
epsilon = 0.9996; alpha = 0.0100
Simulating trial. . . 
epsilon = 0.9996; alpha = 0.0100
Simulating trial. . . 
epsilon = 0.9996; alpha = 0.0100
Simulating trial. . . 
epsilon = 0.9996; alpha = 0.0100
Simulating trial. . . 
epsilon = 0.9996; alpha = 0.0100
Simulating trial. . . 
epsilon = 0.9996; alpha = 0.0100

/-------------------
| Step 0 Results
\-------------------

Environmen

Agent attempted driving forward through a red light. (rewarded -9.46)
10% of time remaining to reach destination.

/-------------------
| Step 18 Results
\-------------------

Environment.step(): t = 18
state variables below
('forward', 'red', None, None)
<built-in method keys of dict object at 0x114faab40>
Environment.act() [POST]: location: (1, 4), heading: (1, 0), action: forward, reward: -10.3488212194
Environment.act(): Step data: {'inputs': {'light': 'red', 'oncoming': None, 'right': None, 'left': None}, 'violation': 2, 'light': 'red', 'state': ('forward', 'red', None, None), 'deadline': 2, 't': 18, 'action': 'forward', 'reward': -10.348821219353553, 'waypoint': 'forward'}
Agent previous state: ('forward', 'red', None, None)
Agent attempted driving forward through a red light. (rewarded -10.35)
5% of time remaining to reach destination.

/-------------------
| Step 19 Results
\-------------------

Environment.step(): t = 19
state variables below
('forward', 'red', None, None)
<bu

...

epsilon = -0.7766; alpha = 0.0100
Simulating trial. . . 
epsilon = -0.7766; alpha = 0.0100
Simulating trial. . . 
epsilon = -0.7766; alpha = 0.0100
Simulating trial. . . 
epsilon = -0.7766; alpha = 0.0100
Simulating trial. . . 
epsilon = -0.7766; alpha = 0.0100
Simulating trial. . . 
epsilon = -0.7766; alpha = 0.0100
Simulating trial. . . 
epsilon = -0.7766; alpha = 0.0100
Simulating trial. . . 
epsilon = -0.7766; alpha = 0.0100
Simulating trial. . . 
epsilon = -0.7766; alpha = 0.0100
Simulating trial. . . 
epsilon = -0.7766; alpha = 0.0100
Simulating trial. . . 
epsilon = -0.7766; alpha = 0.0100
Simulating trial. . . 
epsilon = -0.7766; alpha = 0.0100
Simulating trial. . . 
epsilon = -0.7766; alpha = 0.0100
Simulating trial. . . 
epsilon = -0.7766; alpha = 0.0100
Simulating trial. . . 
epsilon = -0.7766; alpha = 0.0100
Simulating trial. . . 
epsilon = -0.7766; alpha = 0.0100
Simulating trial. . . 
epsilon = -0.7766; alpha = 0.0100
Simulating trial. . . 
epsilon = -0.7766; alpha = 0.01

Simulating trial. . . 
epsilon = -0.7951; alpha = 0.0100
Simulating trial. . . 
epsilon = -0.7951; alpha = 0.0100
Simulating trial. . . 
epsilon = -0.7951; alpha = 0.0100
Simulating trial. . . 
epsilon = -0.7951; alpha = 0.0100
Simulating trial. . . 
epsilon = -0.7951; alpha = 0.0100
Simulating trial. . . 
epsilon = -0.7951; alpha = 0.0100
Simulating trial. . . 
epsilon = -0.7951; alpha = 0.0100
Simulating trial. . . 
epsilon = -0.7951; alpha = 0.0100
Simulating trial. . . 
epsilon = -0.7951; alpha = 0.0100
Simulating trial. . . 
epsilon = -0.7951; alpha = 0.0100
Simulating trial. . . 
epsilon = -0.7951; alpha = 0.0100
Simulating trial. . . 
epsilon = -0.7951; alpha = 0.0100
Simulating trial. . . 
epsilon = -0.7951; alpha = 0.0100
Simulating trial. . . 
epsilon = -0.7951; alpha = 0.0100
Simulating trial. . . 
epsilon = -0.7951; alpha = 0.0100
Simulating trial. . . 
epsilon = -0.7951; alpha = 0.0100
Simulating trial. . . 
epsilon = -0.7951; alpha = 0.0100
Simulating trial. . . 
epsilon 

/-------------------
| Step 1 Results
\-------------------

Environment.step(): t = 1
state variables below
('left', 'green', 'left', 'left')
<built-in method keys of dict object at 0x114faab40>
Environment.act() [POST]: location: (4, 2), heading: (0, 1), action: left, reward: 1.95088173419
Environment.act(): Step data: {'inputs': {'light': 'green', 'oncoming': 'left', 'right': 'forward', 'left': 'left'}, 'violation': 0, 'light': 'green', 'state': ('left', 'green', 'left', 'left'), 'deadline': 19, 't': 1, 'action': 'left', 'reward': 1.9508817341901852, 'waypoint': 'left'}
Agent previous state: ('left', 'green', 'left', 'left')
Agent followed the waypoint left. (rewarded 1.95)
90% of time remaining to reach destination.

/-------------------
| Step 2 Results
\-------------------

Environment.step(): t = 2
state variables below
('left', 'red', None, 'left')
<built-in method keys of dict object at 0x114faab40>
Environment.act() [POST]: location: (4, 2), heading: (0, 1), action: None, rewa

Agent previous state: ('forward', 'green', None, None)
Agent followed the waypoint forward. (rewarded 2.26)
80% of time remaining to reach destination.

/-------------------
| Step 6 Results
\-------------------

Environment.step(): t = 6
state variables below
('forward', 'green', None, None)
<built-in method keys of dict object at 0x114faab40>
Environment.act() [POST]: location: (7, 7), heading: (1, 0), action: forward, reward: 2.06140725757
Environment.act(): Step data: {'inputs': {'light': 'green', 'oncoming': None, 'right': 'left', 'left': None}, 'violation': 0, 'light': 'green', 'state': ('forward', 'green', None, None), 'deadline': 24, 't': 6, 'action': 'forward', 'reward': 2.0614072575702496, 'waypoint': 'forward'}
Agent previous state: ('forward', 'green', None, None)
Agent followed the waypoint forward. (rewarded 2.06)
77% of time remaining to reach destination.

/-------------------
| Step 7 Results
\-------------------

Environment.step(): t = 7
state variables below
('forwa

80% of time remaining to reach destination.

/-------------------
| Step 4 Results
\-------------------

Environment.step(): t = 4
state variables below
('left', 'green', 'forward', None)
<built-in method keys of dict object at 0x114faab40>
Environment.act() [POST]: location: (8, 2), heading: (0, 1), action: forward, reward: 0.699907751435
Environment.act(): Step data: {'inputs': {'light': 'green', 'oncoming': None, 'right': None, 'left': 'forward'}, 'violation': 0, 'light': 'green', 'state': ('left', 'green', 'forward', None), 'deadline': 16, 't': 4, 'action': 'forward', 'reward': 0.699907751435079, 'waypoint': 'left'}
Agent previous state: ('left', 'green', 'forward', None)
Agent drove forward instead of left. (rewarded 0.70)
75% of time remaining to reach destination.

/-------------------
| Step 5 Results
\-------------------

Environment.step(): t = 5
state variables below
('left', 'red', None, None)
<built-in method keys of dict object at 0x114faab40>
Environment.act() [POST]: lo